In [1]:
%matplotlib inline
import warnings
warnings.filterwarnings("ignore")

import numpy as np
import pandas as pd
import tensorflow as tf

from sklearn.model_selection import train_test_split

In [2]:
DATA_PATH = "./data/"
TRAIN_PATH = DATA_PATH + "train.csv"
TEST_PATH = DATA_PATH + "test.csv"
WORD_EMBED_PATH = DATA_PATH + "word_embed.txt"
CHAR_EMBED_PATH = DATA_PATH + "char_embed.txt"
QUEST_PATH = DATA_PATH + "question.csv"

SEED = 2018

In [3]:
train_data = pd.read_csv(TRAIN_PATH)
test_data = pd.read_csv(TEST_PATH)
question_data = pd.read_csv(QUEST_PATH)
word_embedding_data = pd.read_csv(WORD_EMBED_PATH, delimiter=" ", header=None, index_col=0)
char_embedding_data = pd.read_csv(CHAR_EMBED_PATH, delimiter=" ", header=None, index_col=0)

In [4]:
question_data["words"] = question_data["words"].str.split(" ")
question_data["chars"] = question_data["chars"].str.split(" ")

In [5]:
from gensim.corpora import Dictionary

word_dict = Dictionary(question_data["words"])
char_dict = Dictionary(question_data["chars"])

num_words, num_chars = len(word_dict.dfs), len(char_dict.dfs)
num_words, num_chars

(20890, 3048)

In [6]:
def adjust_embedding(embedding, corp_dict):
    index = sorted([k for k, v in corp_dict.token2id.items()], key=lambda x: corp_dict.token2id[x])
    return embedding.reindex(index).values

In [7]:
word_embedding_data = adjust_embedding(word_embedding_data, word_dict)
char_embedding_data = adjust_embedding(char_embedding_data, char_dict)

In [8]:
def pad_embedding(embedding, method="mean"):
    new_vector = np.zeros(embedding.shape[1], dtype=np.float32)
    if method == "mean":
        new_vector = embedding.mean(axis=0)
    return np.concatenate((embedding, new_vector.reshape((1, -1))), axis=0)

In [9]:
print(f"former word embedding matrix shape: {word_embedding_data.shape}")
word_embedding_data = pad_embedding(word_embedding_data, method="zero")
print(f"final word embedding matrix shape: {word_embedding_data.shape}")

print(f"former char embedding matrix shape: {char_embedding_data.shape}")
char_embedding_data = pad_embedding(char_embedding_data, method="zero")
print(f"final char embedding matrix shape: {char_embedding_data.shape}")

former word embedding matrix shape: (20890, 300)
final word embedding matrix shape: (20891, 300)
former char embedding matrix shape: (3048, 300)
final char embedding matrix shape: (3049, 300)


In [10]:
T_STOP = 100000
USE_STOP = True

word_count = sorted([(token, word_dict.dfs[id_]) for token, id_ in word_dict.token2id.items()],
                    key=lambda x: x[1], reverse=True)
char_count = sorted([(token, char_dict.dfs[id_]) for token, id_ in char_dict.token2id.items()],
                    key=lambda x: x[1], reverse=True)

word_stop = [token for token, count in word_count if count >= T_STOP]
char_stop = [token for token, count in char_count if count >= T_STOP]
word_stop, char_stop

(['W17378', 'W19355', 'W16319', 'W18238', 'W18103'],
 ['L0104',
  'L2214',
  'L1861',
  'L2582',
  'L3019',
  'L0143',
  'L2218',
  'L1132',
  'L1128',
  'L0362',
  'L1187'])

In [11]:
def pair2vec(pair, question, use_stop=USE_STOP):
    return ques2vec(pair[["q1"]].rename(columns={"q1": "qid"}), question, use_stop) + \
           ques2vec(pair[["q2"]].rename(columns={"q2": "qid"}), question, use_stop)
    
def ques2vec(ques, question, use_stop=True):
    q = ques.merge(question, how="left", on="qid")
    return seq2vec(q, "words", use_stop), seq2vec(q, "chars", use_stop)
    
def seq2vec(ques, col, use_stop=True):
    seq = ques[col]
    if col == "words":
        d = word_dict.token2id
        s = word_stop
    else:
        d = char_dict.token2id
        s = char_stop
    
    if use_stop:
        return [[d[token] for token in text if token not in s] for text in seq]
    else:
        return [[d[token] for token in text] for text in seq]

In [12]:
train_word1, train_word2, train_char1, train_char2 = pair2vec(train_data, question_data)
test_word1, test_word2, test_char1, test_char2 = pair2vec(test_data, question_data)

In [13]:
T_WORD = 6
T_CHAR = 10

def padding(text, length, pad_index, cut_method):
    text = text[0]
    num_text = len(text)
    if num_text < length:
        return text + [pad_index] * (length - num_text)
    elif num_text > length:
        if cut_method == "direct":
            return text[:length]
        else:
            return text
    return text

def sample_padding(texts, length, pad_index, cut_method="direct"):
    texts = np.array(texts).reshape(-1, 1)
    return np.apply_along_axis(padding, 1, texts, length, pad_index, cut_method="direct")

def padding_all(all_words, all_chars):
    num_words = len(word_dict.dfs)
    num_chars = len(char_dict.dfs)
    words_res = [sample_padding(s, T_WORD, num_words) for s in all_words]
    chars_res = [sample_padding(s, T_CHAR, num_chars) for s in all_chars]
    return tuple(words_res + chars_res)

In [14]:
train_word1, train_word2, train_char1, train_char2 = padding_all([train_word1, train_word2], [train_char1, train_char2])
test_word1, test_word2, test_char1, test_char2 = padding_all([test_word1, test_word2], [test_char1, test_char2])

In [15]:
train_word1, dev_word1, \
train_word2, dev_word2, \
train_char1, dev_char1, \
train_char2, dev_char2, \
train_y, dev_y = train_test_split(train_word1, train_word2, train_char1, train_char2, train_data["label"], test_size=0.05)

In [16]:
# epoch = 10
# batch_size = 256
# keep_prob = 0.8
# unit_size = 128
# dense_size = 64
# learning_rate = 0.05
# clip_norm = 2
# weight_init = 0.1


# def lstm_cell(unit_size, keep):
#     lstm = tf.contrib.rnn.BasicLSTMCell(unit_size)
#     drop = tf.contrib.rnn.DropoutWrapper(lstm, output_keep_prob=keep)
#     return drop

# graph = tf.Graph()
# with graph.as_default():
#     with tf.variable_scope("dataset"):
#         dataset = tf.data.Dataset.from_tensor_slices((train_word1, train_word2, train_char1, train_char2, train_y))
#         dataset = dataset.repeat(epoch).shuffle(batch_size * 3 + 1000).batch(batch_size)
#         iterator = dataset.make_initializable_iterator()
#         word1, word2, char1, char2, label = iterator.get_next()
    
#     with tf.variable_scope("input"):
#         w1 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w1")
#         w2 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w2")
#         c1 = tf.placeholder(shape=(None, T_CHAR), dtype=tf.int64, name="c1")
#         c2 = tf.placeholder(shape=(None, T_CHAR), dtype=tf.int64, name="c2")
#         y = tf.placeholder(shape=(None,), dtype=tf.float64, name="y_true")
#         keep = tf.placeholder(shape=(), dtype=tf.float64, name="keep_prob")
    
#     with tf.variable_scope("embedding"):
#         word_embedding = tf.Variable(word_embedding_data, trainable=False, name="word_embedding")
#         char_embedding = tf.Variable(char_embedding_data, trainable=False, name="char_embedding")
#         w1_embed = tf.nn.embedding_lookup(word_embedding, w1, name="word1_embed")
#         w2_embed = tf.nn.embedding_lookup(word_embedding, w2, name="word2_embed")
#         c1_embed = tf.nn.embedding_lookup(char_embedding, c1, name="char1_embed")
#         c2_embed = tf.nn.embedding_lookup(char_embedding, c2, name="char2_embed")
    
#     with tf.variable_scope("word_layers"):
#         word_cell = lstm_cell(unit_size, keep)
#         output_w1, _ = tf.nn.dynamic_rnn(word_cell, w1_embed, dtype=tf.float64)
#         output_w2, _ = tf.nn.dynamic_rnn(word_cell, w2_embed, dtype=tf.float64)
    
#     with tf.variable_scope("char_layers"):
#         char_cell = lstm_cell(unit_size, keep)
#         output_c1, _ = tf.nn.dynamic_rnn(char_cell, c1_embed, dtype=tf.float64)
#         output_c2, _ = tf.nn.dynamic_rnn(char_cell, c2_embed, dtype=tf.float64)
        
#     with tf.variable_scope("combination"):
#         o_w1, o_w2 = output_w1[:, -1, :], output_w2[:, -1, :]
#         o_c1, o_c2 = output_c1[:, -1, :], output_c2[:, -1, :]
#         final_output = tf.concat((o_w1, o_w2, o_c1, o_c2), axis=1)
    
# #     with tf.variable_scope("output_layer"):
# #         dense_output = tf.layers.dense(final_output, dense_size, activation=tf.nn.relu,
# #                                        kernel_initializer=tf.truncated_normal_initializer(stddev=weight_init),
# #                                        bias_initializer=tf.zeros_initializer)
# #         pred = tf.layers.dense(dense_output, 1,
# #                                activation=tf.nn.sigmoid, kernel_initializer=tf.truncated_normal_initializer(stddev=weight_init),
# #                                bias_initializer=tf.zeros_initializer)
#     with tf.variable_scope("output_layer"):
#         pred = tf.layers.dense(final_output, 1,
#                                activation=tf.nn.sigmoid, kernel_initializer=tf.truncated_normal_initializer(stddev=weight_init),
#                                bias_initializer=tf.zeros_initializer)
    
#     with tf.variable_scope("loss"):
#         loss = -tf.reduce_mean(y * tf.log(pred) + (1 - y) * tf.log(1 - pred))
        
#     with tf.variable_scope("train"):
#         global_step = tf.Variable(0, trainable=False, dtype=tf.int64, name="global_step")
#         optimizer = tf.train.AdamOptimizer(learning_rate=learning_rate)
#         grads, variables = zip(*optimizer.compute_gradients(loss, tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES)))
# #         clip_grads = tf.clip_by_global_norm(grads, clip_norm)[0]
#         train_op = optimizer.apply_gradients(zip(grads, variables), global_step=global_step)
# #         train_op = optimizer.minimize(loss, global_step=global_step)

#     tf.summary.scalar("batch_loss", loss)
#     for v in tf.trainable_variables():
#         tf.summary.histogram(v.name, v)
#     for g in grads:
#         tf.summary.histogram("grad_" + g.name, g)
    
#     writer = tf.summary.FileWriter("./log/", graph=graph)

# with tf.Session(graph=graph) as sess:
#     tf.global_variables_initializer().run()
#     tf.local_variables_initializer().run()
#     sess.run(iterator.initializer)
    
#     summary_op = tf.summary.merge_all()
    
#     try:
#         while True:
#             res_w1, res_w2, res_c1, res_c2, res_y = sess.run([word1, word2, char1, char2, label])
#             train_feed = {
#                 w1: res_w1,
#                 w2: res_w2,
#                 c1: res_c1,
#                 c2: res_c2,
#                 y: res_y,
#                 keep: keep_prob,
#             }
            
#             _, total_steps, train_loss = sess.run([train_op, global_step, loss], feed_dict=train_feed)
# #             _, total_steps, train_loss, summary = sess.run([train_op, global_step, loss, summary_op], feed_dict=train_feed)
# #             writer.add_summary(summary, global_step=total_steps)
            
#             if total_steps % 100  == 0:
#                 test_feed = {
#                     w1: dev_word1,
#                     w2: dev_word2,
#                     c1: dev_char1,
#                     c2: dev_char2,
#                     y: dev_y,
#                     keep: 1.0,
#                 }
#                 dev_less = sess.run(loss, feed_dict=test_feed)
                
#                 print(f"[step {total_steps}] train loss: {train_loss}, dev loss: {dev_less}")
#     except tf.errors.OutOfRangeError:
#         pass

In [24]:
# epoch = 10
# batch_size = 128
# keep_prob = 0.8
# unit_size = 64
# dense_size = 64
# learning_rate = 10
# clip_norm = 5
# weight_init = 0.1


# def lstm_cell(unit_size, keep):
#     lstm = tf.contrib.rnn.BasicLSTMCell(unit_size)
#     drop = tf.contrib.rnn.DropoutWrapper(lstm, output_keep_prob=keep)
#     return drop

# graph = tf.Graph()
# with graph.as_default():
#     with tf.variable_scope("dataset"):
#         dataset = tf.data.Dataset.from_tensor_slices((train_word1, train_word2, train_y))
#         dataset = dataset.repeat(epoch).shuffle(batch_size * 3 + 1000).batch(batch_size)
#         iterator = dataset.make_initializable_iterator()
#         word1, word2, label = iterator.get_next()
    
#     with tf.variable_scope("input"):
#         w1 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w1")
#         w2 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w2")
#         y = tf.placeholder(shape=(None,), dtype=tf.float64, name="y_true")
#         keep = tf.placeholder(shape=(), dtype=tf.float64, name="keep_prob")
    
#     with tf.variable_scope("embedding"):
#         word_embedding = tf.Variable(word_embedding_data, trainable=False, name="word_embedding")
#         w1_embed = tf.nn.embedding_lookup(word_embedding, w1, name="word1_embed")
#         w2_embed = tf.nn.embedding_lookup(word_embedding, w2, name="word2_embed")
        
#     with tf.variable_scope("word_layers"):
#         word_cell = lstm_cell(unit_size, keep)
#         output_w1, _ = tf.nn.dynamic_rnn(word_cell, w1_embed, dtype=tf.float64)
#         output_w2, _ = tf.nn.dynamic_rnn(word_cell, w2_embed, dtype=tf.float64)
        
#     with tf.variable_scope("combination"):
#         o_w1, o_w2 = output_w1[:, -1, :], output_w2[:, -1, :]
#         final_output = tf.concat((o_w1, o_w2), axis=1)
    
#     with tf.variable_scope("output_layer"):
#         pred = tf.layers.dense(final_output, 1,
#                                activation=tf.nn.sigmoid, kernel_initializer=tf.truncated_normal_initializer(stddev=weight_init),
#                                bias_initializer=tf.zeros_initializer)
    
#     with tf.variable_scope("loss"):
#         loss = -tf.reduce_mean(y * tf.log(pred) + (1 - y) * tf.log(1 - pred))
        
#     with tf.variable_scope("train"):
#         global_step = tf.Variable(0, trainable=False, dtype=tf.int64, name="global_step")
#         optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
#         grads, variables = zip(*optimizer.compute_gradients(loss, tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES)))
#         clip_grads = tf.clip_by_global_norm(grads, clip_norm)[0]
#         train_op = optimizer.apply_gradients(zip(clip_grads, variables), global_step=global_step)

#     tf.summary.scalar("batch_loss", loss)
#     writer = tf.summary.FileWriter("./log/", graph=graph)


# with tf.Session(graph=graph) as sess:
#     tf.global_variables_initializer().run()
#     tf.local_variables_initializer().run()
#     sess.run(iterator.initializer)
    
#     summary_op = tf.summary.merge_all()
    
#     try:
#         while True:
#             res_w1, res_w2, res_y = sess.run([word1, word2, label])
#             train_feed = {
#                 w1: res_w1,
#                 w2: res_w2,
#                 y: res_y,
#                 keep: keep_prob,
#             }
#             _, total_steps, train_loss, summary = sess.run([train_op, global_step, loss, summary_op], feed_dict=train_feed)
#             writer.add_summary(summary, global_step=total_steps)
            
# #             res_grads = sess.run(clip_grads, feed_dict=train_feed)
            
#             if total_steps % 100  == 0:
#                 test_feed = {
#                     w1: dev_word1,
#                     w2: dev_word2,
#                     y: dev_y,
#                     keep: 1.0,
#                 }
#                 dev_less = sess.run(loss, feed_dict=test_feed)
                
#                 print(f"[step {total_steps}] train loss: {train_loss}, dev loss: {dev_less}")
#     except tf.errors.OutOfRangeError:
#         print("train finished")

[[[-1.8804816   0.38268623  1.54164696 ...  3.039042   -2.07602429
    1.35068381]
  [-0.39968655 -1.03601968 -1.69233811 ...  1.91834378  1.72091699
   -1.59328139]
  [-0.2754727   1.76645207 -1.00754213 ... -2.87295818  0.43883628
    2.03410101]
  [-0.94895422 -0.81354105 -1.64983642 ... -0.64164656 -1.07170463
   -1.75714469]
  [-6.10933447  1.89827943  1.29533637 ... -1.79521418  2.43789601
    0.167372  ]
  [ 2.74516964 -1.97532105  3.99819613 ...  6.76446629 -2.12120771
   -0.14509301]]

 [[ 0.74529082 -2.70321059  5.12112808 ...  5.70591068 -3.78293347
    5.37727451]
  [-0.96980548  3.49921417  0.62349629 ...  5.48152113 -1.27842045
   -3.10639668]
  [-2.96462297 -1.86708438 -0.4626489  ... -0.93833709 -4.46298456
    1.68966281]
  [-1.8804816   0.38268623  1.54164696 ...  3.039042   -2.07602429
    1.35068381]
  [ 3.39893317  1.63210154 -4.51659632 ...  1.79811776 -1.21029449
    0.9941867 ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[ 0.46

   -1.14479053]]]
[[[-0.27296099  1.49044907 -0.54831398 ... -1.8940556   0.84029299
    0.03187116]
  [ 0.57804674 -1.44180024 -1.13911533 ... -1.90609539 -0.10874847
    1.22401094]
  [ 0.73045921 -4.73640776 -0.60518438 ... -0.72813302  0.61311477
    1.05554664]
  [ 3.84536505  2.42206883  2.48941565 ... -3.00344896 -0.12113728
   -1.41772032]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[-0.64529914  2.07171607 -3.05682945 ... -0.74891132  1.91205835
   -2.70767665]
  [ 4.25564289 -1.03822315  3.02172256 ...  1.90380144  2.79290652
    0.7174902 ]
  [-1.07393765  0.92020231  3.04805732 ... -1.81790149 -0.30004713
    0.31312716]
  [-0.2754727   1.76645207 -1.00754213 ... -2.87295818  0.43883628
    2.03410101]
  [ 0.49685487  1.63047445  3.75343657 ... -2.40251517  4.56101894
   -1.35709286]
  [ 3.68629766 -0.19609913  2.06685495 ...  1.56823826 -2.15131521
   -1.4763608 ]]

[[[-6.10933447  1.89827943  1.29533637 ... -1.79521418  2.43789601
    0.167372  ]
  [ 0.91234261 -0.10402886  0.2975505  ... -0.06265366 -2.08243537
    2.10736489]
  [-0.79729527 -0.68095326  0.76599669 ...  0.14573619  0.54900271
    1.7506665 ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[ 2.05238271 -2.37914681 -2.44720459 ...  1.12406611  0.66053993
    1.61141992]
  [ 3.24178886 -0.59638131  0.120327   ...  0.31965837 -0.54641598
    4.70198107]
  [ 0.47914824 -0.89298862 -0.72203243 ... -0.22452596 -1.853526
    1.13275838]
  [-0.64529914  2.07171607 -3.05682945 ... -0.74891132  1.91205835
   -2.70767665]
  [-0.28585666 -0.64593381  0.1022184  ... -1.08646095 -0.43330649
    0.16530415]
  [ 1.74433851 -2.42554712  1.17229342 ...  0.89760786  1.13769722
    3.11923456]]

 [[ 2.1826334   4.06378412

    0.        ]]]
[[[ 2.52785500e-01 -2.91632175e+00  1.35264122e+00 ...  7.17572630e-01
    1.70120168e+00  1.38426614e+00]
  [-1.98541975e+00  3.84606240e-01  5.00046396e+00 ...  2.32288074e+00
   -1.69550200e-02  5.93781890e-01]
  [-2.75342393e+00 -4.52579117e+00 -2.12757802e+00 ...  3.24414515e+00
    4.04914140e-01  1.97592366e+00]
  [-2.96462297e+00 -1.86708438e+00 -4.62648900e-01 ... -9.38337090e-01
   -4.46298456e+00  1.68966281e+00]
  [-2.86545420e+00  2.01143122e+00 -1.49399161e+00 ... -1.13536179e+00
    1.61745453e+00  2.01484251e+00]
  [-2.30203414e+00  2.01556706e+00 -1.54739320e+00 ... -1.48318863e+00
   -3.09319019e+00 -6.84266030e-01]]

 [[-5.07700260e-01 -9.86308990e-01  2.43345308e+00 ...  1.02304661e+00
   -3.04252958e+00  3.23458648e+00]
  [-3.11764200e-02  1.02335119e+00  6.21021557e+00 ...  2.54615402e+00
   -5.01201810e-01 -2.92880535e+00]
  [ 3.63886786e+00  1.50119889e+00 -1.91523480e+00 ...  6.40430117e+00
   -4.99002838e+00 -5.42382900e-02]
  [-3.31107068e+0

    0.        ]]]
[[[ 0.05374239 -3.1234889  -2.64408112 ...  2.55207658  1.70188582
   -0.43103519]
  [-0.39968655 -1.03601968 -1.69233811 ...  1.91834378  1.72091699
   -1.59328139]
  [-2.85813999  2.43923616 -1.69941688 ... -1.67861032  0.34405875
    0.50072527]
  [-2.19903612 -0.4767417   0.80386728 ...  3.24631023  1.89588535
   -5.07398033]
  [ 0.57804674 -1.44180024 -1.13911533 ... -1.90609539 -0.10874847
    1.22401094]
  [ 2.17861557 -0.05671161 -0.23705147 ...  0.73785943 -0.48526677
   -0.30371439]]

 [[ 0.1388123  -3.89070678 -1.62941277 ...  0.50355512 -1.62632895
   -5.26311827]
  [-1.14515364 -0.08780726  0.82729858 ... -3.36786914 -1.35945356
    0.43744218]
  [ 2.9471159   4.62252951  1.84169614 ... -2.42791152 -2.86602831
   -0.38987347]
  [-3.22455096  0.98420626 -2.70284605 ...  0.49715263 -0.76476157
   -4.63694954]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

...

[[[ 3.68629766 -0.19609913  2.06685495 ...  1.56823826 -2.15131521
   -1.4763608 ]
  [-4.72215366 -2.23823261 -1.91102576 ... -0.48909608  0.37598708
   -0.11034796]
  [ 0.05374239 -3.1234889  -2.64408112 ...  2.55207658  1.70188582
   -0.43103519]
  [-0.39968655 -1.03601968 -1.69233811 ...  1.91834378  1.72091699
   -1.59328139]
  [-1.96389675 -1.71115243 -1.70632231 ... -3.23301005 -0.51847482
   -1.14479053]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[-1.8440094   3.96981335 -2.2352078  ... -2.33095431 -1.42540622
   -1.06833398]
  [-1.56378353  2.24956059 -1.68607736 ...  2.71622753  0.74901795
   -6.8169241 ]
  [ 4.17974281 -0.39201459  4.75850916 ...  6.48030567 -5.2377553
    6.39069986]
  [ 0.49654543 -1.31683779 -0.43108895 ...  6.78044701  5.00765657
   -0.90496308]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[-2.75342393 -4.5257911

    0.        ]]]
[[[ 0.16817473 -1.88535643  3.23685527 ... -2.05766249  1.25098407
    4.44117832]
  [-0.58008784  1.54624808 -0.24854569 ...  3.63826513 -0.89585048
    2.82505393]
  [ 0.29744378  3.43959498 -0.4960587  ... -0.77938235  1.97591066
    1.16438758]
  [ 3.68629766 -0.19609913  2.06685495 ...  1.56823826 -2.15131521
   -1.4763608 ]
  [ 0.28289089 -1.06511974 -1.32498014 ...  2.42743087 -1.47657478
    1.51878977]
  [-1.96389675 -1.71115243 -1.70632231 ... -3.23301005 -0.51847482
   -1.14479053]]

 [[-5.01347733  1.81552768 -0.75234962 ... -1.66974092 -0.10116684
   -1.91881716]
  [-1.90061975 -2.71826077  0.51707375 ...  2.25202584  1.25725842
   -1.1981349 ]
  [-0.39968655 -1.03601968 -1.69233811 ...  1.91834378  1.72091699
   -1.59328139]
  [-2.06454468 -0.29292467  1.67147076 ...  0.69536471  3.5697186
   -4.54786682]
  [ 3.04128647 -4.48644161  0.48715267 ... -0.65614033  3.01616406
    1.11952734]
  [ 0.          0.          0.         ...  0.          0.
    0.   

[[[-1.17170918 -1.94284463  0.36973056 ...  4.22560263  1.09641969
   -1.12657857]
  [-2.40768337 -0.78683162  1.4735955  ...  3.28996205  2.48009992
   -0.9441222 ]
  [ 0.9875229  -1.67870629  0.50348753 ... -2.69120574  2.01527572
   -1.1237967 ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[-3.13644648  2.24466681 -2.08086967 ... -0.41840655  0.5415442
   -0.53036112]
  [ 1.02723885 -1.44202769 -0.98994577 ...  0.58279723 -0.85889935
    0.2727218 ]
  [ 1.98205769  2.84459829 -0.88892931 ... -0.83251381 -1.37395477
    2.98363161]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[ 1.71453822 -1.167153   -3.22897458 ...  1.105

[[[-1.61103404  1.66478467  0.55347943 ... -2.41827917 -0.25171506
   -0.629987  ]
  [-0.24062829  1.32125294 -0.8096633  ... -0.29809567 -0.38124987
    0.72002137]
  [-0.74293417 -1.23761141 -1.37281442 ... -0.60563916 -1.9088459
   -3.27147865]
  [-1.98639309 -1.94278109 -2.15081263 ...  1.98048711 -1.08504617
    1.49992073]
  [ 0.21888028  0.13161106  0.68905497 ... -0.92721355 -0.98295128
    1.5115788 ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[-0.2754727   1.76645207 -1.00754213 ... -2.87295818  0.43883628
    2.03410101]
  [-5.02900076  0.07521021  1.853055   ... -5.18241215  0.19779301
    3.1882658 ]
  [ 4.13393974 -4.67355442  0.90743172 ...  5.36845016 -4.84133339
    1.27279711]
  [-0.63266402 -1.27675378 -2.14357471 ... -2.89202499  0.67571461
   -2.06400275]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]
  [ 0.          0.          0.         ...  0.          0.
    0.        ]]

 [[-2.83723211 -0.3955762

KeyboardInterrupt: 

In [34]:
# epoch = 10
# batch_size = 128
# keep_prob = 0.8
# unit_size = 64
# dense_size = 64
# learning_rate = 1
# clip_norm = 5
# weight_init = 0.1


# def lstm_cell(unit_size, keep):
#     lstm = tf.contrib.rnn.BasicLSTMCell(unit_size)
#     drop = tf.contrib.rnn.DropoutWrapper(lstm, output_keep_prob=keep)
#     return drop

# graph = tf.Graph()
# with graph.as_default():
#     with tf.variable_scope("dataset"):
#         dataset = tf.data.Dataset.from_tensor_slices((train_word1, train_word2, train_y))
#         dataset = dataset.repeat(epoch).shuffle(batch_size * 3 + 1000).batch(batch_size)
#         iterator = dataset.make_initializable_iterator()
#         word1, word2, label = iterator.get_next()
    
#     with tf.variable_scope("input"):
#         w1 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w1")
#         w2 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w2")
#         y = tf.placeholder(shape=(None,), dtype=tf.float64, name="y_true")
#         keep = tf.placeholder(shape=(), dtype=tf.float64, name="keep_prob")
    
#     with tf.variable_scope("embedding"):
#         word_embedding = tf.Variable(word_embedding_data, trainable=False, name="word_embedding")
#         w1_embed = tf.nn.embedding_lookup(word_embedding, w1, name="word1_embed")
#         w2_embed = tf.nn.embedding_lookup(word_embedding, w2, name="word2_embed")
#         word_input = w1_embed - w2_embed
        
#     with tf.variable_scope("word_layers"):
#         word_cell = lstm_cell(unit_size, keep)
#         output_word, _ = tf.nn.dynamic_rnn(word_cell, word_input, dtype=tf.float64)
        
#     with tf.variable_scope("combination"):
#         final_output = output_word[:, -1, :]
    
#     with tf.variable_scope("output_layer"):
#         pred = tf.layers.dense(final_output, 1, activation=tf.nn.sigmoid,
#                                kernel_initializer=tf.truncated_normal_initializer(stddev=weight_init),
#                                bias_initializer=tf.zeros_initializer)
    
#     with tf.variable_scope("loss"):
#         loss = -tf.reduce_mean(y * tf.log(pred) + (1 - y) * tf.log(1 - pred))
        
#     with tf.variable_scope("train"):
#         global_step = tf.Variable(0, trainable=False, dtype=tf.int64, name="global_step")
#         optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
#         grads, variables = zip(*optimizer.compute_gradients(loss, tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES)))
#         clip_grads = tf.clip_by_global_norm(grads, clip_norm)[0] * 100
#         train_op = optimizer.apply_gradients(zip(clip_grads, variables), global_step=global_step)

#     tf.summary.scalar("batch_loss", loss)
#     writer = tf.summary.FileWriter("./log/", graph=graph)


# with tf.Session(graph=graph) as sess:
#     tf.global_variables_initializer().run()
#     tf.local_variables_initializer().run()
#     sess.run(iterator.initializer)
    
#     summary_op = tf.summary.merge_all()
    
#     try:
#         while True:
#             res_w1, res_w2, res_y = sess.run([word1, word2, label])
#             train_feed = {
#                 w1: res_w1,
#                 w2: res_w2,
#                 y: res_y,
#                 keep: keep_prob,
#             }
#             _, total_steps, train_loss, summary = sess.run([train_op, global_step, loss, summary_op], feed_dict=train_feed)
#             writer.add_summary(summary, global_step=total_steps)
            
#             res_grads = sess.run(clip_grads, feed_dict=train_feed)
#             grads_sum = [res.sum() for res in res_grads]
#             print(grads_sum)
            
#             if total_steps % 100  == 0:
#                 test_feed = {
#                     w1: dev_word1,
#                     w2: dev_word2,
#                     y: dev_y,
#                     keep: 1.0,
#                 }
#                 dev_less = sess.run(loss, feed_dict=test_feed)
                
#                 print(f"[step {total_steps}] train loss: {train_loss}, dev loss: {dev_less}")
#     except tf.errors.OutOfRangeError:
#         print("train finished")

[step 100] train loss: 0.6930426605785187, dev loss: 0.6925282767579445
[step 200] train loss: 0.6874176666074551, dev loss: 0.6928374649042208
[step 300] train loss: 0.6988575386477581, dev loss: 0.692736821826098
[step 400] train loss: 0.6987893282421667, dev loss: 0.692362749995458
[step 500] train loss: 0.6908406429151057, dev loss: 0.6923506373415691


KeyboardInterrupt: 

In [56]:
epoch = 10
batch_size = 128
keep_prob = 0.8
unit_size = 64
dense_size = 64
learning_rate = 0.01
clip_norm = 5
weight_init = 0.1


def lstm_cell(unit_size, keep):
    lstm = tf.contrib.rnn.BasicLSTMCell(unit_size)
    drop = tf.contrib.rnn.DropoutWrapper(lstm, output_keep_prob=keep)
    return drop

graph = tf.Graph()
with graph.as_default():    
    with tf.variable_scope("input"):
        w1 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w1")
        w2 = tf.placeholder(shape=(None, T_WORD), dtype=tf.int64, name="w2")
        y = tf.placeholder(shape=(None,), dtype=tf.float64, name="y_true")
        keep = tf.placeholder(shape=(), dtype=tf.float64, name="keep_prob")
    
    with tf.variable_scope("embedding"):
        word_embedding = tf.Variable(word_embedding_data, trainable=False, name="word_embedding")
        w1_embed = tf.nn.embedding_lookup(word_embedding, w1, name="word1_embed")
        w2_embed = tf.nn.embedding_lookup(word_embedding, w2, name="word2_embed")
        word_input = w1_embed - w2_embed
        
    with tf.variable_scope("word_layers"):
        word_cell = lstm_cell(unit_size, keep)
        output_word, _ = tf.nn.dynamic_rnn(word_cell, word_input, dtype=tf.float64)
        
    with tf.variable_scope("combination"):
        final_output = output_word[:, -1, :]
    
    with tf.variable_scope("output_layer"):
        pred = tf.layers.dense(final_output, 1, activation=tf.nn.sigmoid,
                               kernel_initializer=tf.truncated_normal_initializer(stddev=weight_init),
                               bias_initializer=tf.zeros_initializer)
    
    with tf.variable_scope("loss"):
        loss = -tf.reduce_mean(y * tf.log(pred) + (1 - y) * tf.log(1 - pred))
        
    with tf.variable_scope("train"):
        global_step = tf.Variable(0, trainable=False, dtype=tf.int64, name="global_step")
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
#         train_op = optimizer.minimize(loss, global_step=global_step)
        grads, variables = zip(*optimizer.compute_gradients(loss, tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES)))
        train_op = optimizer.apply_gradients(zip(grads, variables), global_step=global_step)
#         clip_grads = tf.clip_by_global_norm(grads, clip_norm)[0]
#         train_op = optimizer.apply_gradients(zip(clip_grads, variables), global_step=global_step)

    tf.summary.scalar("batch_loss", loss)
    writer = tf.summary.FileWriter("./log/", graph=graph)

num_epoch = 10
num_batch = 128
num_train = len(train_word1)

with tf.Session(graph=graph) as sess:
    tf.global_variables_initializer().run()
    
    summary_op = tf.summary.merge_all()
    
    for epoch in range(num_epoch):
        epoch_index = np.random.permutation(num_train)
        for i in range(num_train // num_batch):
            batch_index = epoch_index[i * num_batch: (i + 1) * num_batch]
            data_w1 = train_word1[batch_index, :]
            data_w2 = train_word1[batch_index, :]
            data_y = train_y[batch_index]

            train_feed = {w1: data_w1, w2: data_w2, y: data_y, keep: keep_prob}
            res = sess.run([w1_embed, train_op, global_step, loss, summary_op] + list(variables) + list(grads),
                           feed_dict=train_feed)
            print("-"*60)
            print(res[5:9])
            print("-"*60)
            print(res[9:])
            
#             if total_steps % 100  == 0:
#                 test_feed = {
#                     w1: dev_word1,
#                     w2: dev_word2,
#                     y: dev_y,
#                     keep: 1.0,
#                 }
#                 dev_less = sess.run(loss, feed_dict=test_feed)
#                 print(f"[step {total_steps}] train loss: {train_loss}, dev loss: {dev_less}")
#                 print(res1)
            break
        break

[array([[-0.07778381, -0.01257139, -0.03097936, ...,  0.0074324 ,
         0.00347583,  0.04184855],
       [-0.04618976,  0.00089299, -0.07046211, ..., -0.01850976,
        -0.04981612,  0.04515448],
       [-0.0008267 , -0.06070106,  0.02192193, ..., -0.0827329 ,
         0.02086877, -0.06997622],
       ...,
       [-0.05509098,  0.00081895,  0.01658969, ...,  0.06663301,
         0.00088618, -0.07862129],
       [-0.04034873, -0.022217  ,  0.00762835, ..., -0.04795921,
         0.00551454, -0.03912432],
       [-0.01761955,  0.01774952,  0.09605784, ..., -0.02259775,
        -0.09644335,  0.07969846]]), array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
       0.,